In [1]:
from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [2]:
%%capture
!pip install transformers

In [3]:
import torch
import numpy as np
import pandas as pd
import torch.nn as nn

import transformers
from sklearn.metrics import *
from transformers import AdamW
from tqdm.notebook import tqdm
from scipy.special import softmax
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split as tts
from transformers import BertTokenizerFast, BertConfig, BertForSequenceClassification, AutoModel
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

In [4]:
# Define the device
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

#### Download

In [5]:
cd drive/My Drive/Colab Notebooks/experiments

/content/drive/My Drive/Colab Notebooks/experiments


In [6]:
# Download humor detection data
# Paper: https://arxiv.org/abs/2004.12765
data = pd.read_csv("data/trofi.csv")
print("\nThere are", len(data), "sentences")

# Use the standard text/label columns
# Create labels: 1 --> humorous, 0 --> not humorous
data["label"] = data["label"].apply(int)
data.head()


There are 3737 sentences


verb                                           sentence  verb_idx  label
0  absorb  An Energy Department spokesman says the sulfur...        22      0
1  absorb  The yellow beta carotene pigment absorbs blue ...         5      0
2  absorb  This time , the ground absorbed the shock wave...         5      0
3  absorb  '' Vitamins could be passed right out of the b...        12      0
4  absorb  As Eliot wrote : '' In a warm haze , the sultr...        14      0

#### Split to training, validation and test



In [7]:
# Use a subset for quick experiments
#subset_data = data[:10000]

# Split to train, val and test
train, test = tts(data[["sentence", "label"]], random_state=42, test_size=0.1)
train, val = tts(train, random_state=42, test_size=test.shape[0])

#### Tokenize and encode with BERT tokenizer

In [8]:
# Construct a BERT tokenizer based on WordPiece
bert_tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')

In [9]:
# A sanity check of the tokenizer
encoded_instance = bert_tokenizer.batch_encode_plus([train.iloc[0].sentence], padding=True)
print(encoded_instance)

{'input_ids': [[101, 2061, 2057, 1005, 2128, 8040, 17686, 1996, 3663, 1010, 10209, 2067, 1010, 1998, 2035, 1997, 1037, 5573, 2023, 3124, 4152, 2023, 9577, 8460, 1010, 2059, 2515, 1037, 2440, 1011, 2006, 13297, 14257, 2121, 1010, 2059, 1037, 2440, 1011, 2006, 10236, 24490, 3013, 5963, 1010, 2059, 1037, 2440, 1011, 2006, 10245, 2128, 4765, 2854, 102]], 'token_type_ids': [[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]]}


In [10]:
print("Original text:", train.iloc[0].sentence)
print("BERT BPEs:", bert_tokenizer.convert_ids_to_tokens(encoded_instance["input_ids"][0]))

Original text: So we 're scoping the situation , kicking back , and all of a sudden this guy gets this insane barrel , then does a full - on airplane floater , then a full - on wraparound cutback , then a full - on snap reentry 
BERT BPEs: ['[CLS]', 'so', 'we', "'", 're', 'sc', '##oping', 'the', 'situation', ',', 'kicking', 'back', ',', 'and', 'all', 'of', 'a', 'sudden', 'this', 'guy', 'gets', 'this', 'insane', 'barrel', ',', 'then', 'does', 'a', 'full', '-', 'on', 'airplane', 'float', '##er', ',', 'then', 'a', 'full', '-', 'on', 'wrap', '##around', 'cut', '##back', ',', 'then', 'a', 'full', '-', 'on', 'snap', 're', '##ent', '##ry', '[SEP]']


In [11]:
# Set max_len to the maximum length of the training data 
max_len = max([len(bert_tokenizer.encode(s)) for s in train.sentence.to_list()])
print("The maximum sentence length in training based on BERT BPEs is", max_len)

The maximum sentence length in training based on BERT BPEs is 112


In [12]:
# Tokenize and encode sentences in each set
x_train = bert_tokenizer.batch_encode_plus(
    train.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_val = bert_tokenizer.batch_encode_plus(
    val.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_test = bert_tokenizer.batch_encode_plus(
    test.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)

In [13]:
# Convert lists to tensors in order to feed them to our PyTorch model
train_seq = torch.tensor(x_train['input_ids'])
train_mask = torch.tensor(x_train['attention_mask'])
train_y = torch.tensor(train.label.tolist())

val_seq = torch.tensor(x_val['input_ids'])
val_mask = torch.tensor(x_val['attention_mask'])
val_y = torch.tensor(val.label.tolist())

test_seq = torch.tensor(x_test['input_ids'])
test_mask = torch.tensor(x_test['attention_mask'])
test_y = torch.tensor(test.label.tolist())

In [14]:
batch_size = 32

# Create a dataloader for each set

# TensorDataset: Creates a PyTorch dataset object to load data from
train_data = TensorDataset(train_seq, train_mask, train_y)
# RandomSampler: specify the sequence of indices/keys used in data loading
train_sampler = RandomSampler(train_data)
# DataLoader: a Python iterable over a dataset
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

val_data = TensorDataset(val_seq, val_mask, val_y)
val_sampler = SequentialSampler(val_data)
val_dataloader = DataLoader(val_data, sampler=val_sampler, batch_size=batch_size)

test_data = TensorDataset(test_seq, test_mask, test_y)
test_sampler = SequentialSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=1)

## Build and train the model

In [15]:
# Define which BERT model to use
# We will use BERT base pre-trained on uncased text
model_name = "bert-base-uncased"
# The BertForSequenceClassification class creates a model with BERT and a classifier on top
# The classifier is a linear layer with two outputs (two is the default, if you have more labels change the config)
# It uses the CrossEntropyLoss from PyTorch
# from_pretrained() is used to load pre-trained weights
model = BertForSequenceClassification.from_pretrained(model_name, output_attentions=True)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

In [16]:
# Training method
def training():
  # Set to train mode
  model.train()
  total_loss, total_accuracy = 0, 0
  # Iterate through the training batches
  for batch in tqdm(train_dataloader, desc="Iteration"):    
    # Push the batch to gpu
    batch = [r.to(device) for r in batch] 
    sent_id, mask, labels = batch
    # Clear gradients 
    model.zero_grad()
    # Get model outputs
    outputs = model(sent_id, attention_mask=mask, labels=labels)
    # Get loss
    loss = outputs.loss
    # Add to the total loss
    total_loss = total_loss + loss
    # Backward pass to calculate the gradients
    loss.backward()
    # Update parameters
    optimizer.step()
  # Compute the training loss of the epoch
  epoch_loss = total_loss / len(train_dataloader)

  return epoch_loss

In [17]:
# Evaluation method
def evaluate():  
  print("\nEvaluating...")  
  # Set to eval mode
  model.eval()
  total_loss, total_accuracy = 0, 0
  predictions, targets = [], []
  # Iterate through the validation batches
  for batch in val_dataloader:
    # Push the batch to gpu
    batch = [t.to(device) for t in batch]
    sent_id, mask, labels = batch
    # Save the gold labels to use them for evaluation
    targets.extend(labels.detach().cpu().numpy())
    # Deactivate autograd
    with torch.no_grad():
      # Get model outputs
      outputs = model(sent_id, attention_mask=mask, labels=labels)
      # Get loss
      loss = outputs.loss
      total_loss = total_loss + loss
      # Apply softmax to the output of the model
      output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
      # Get the index with the largest probability as the predicted label
      predictions.extend(np.argmax(output_probs, axis=1))
  # Compute the validation loss of the epoch
  epoch_loss = total_loss / len(val_dataloader)

  return epoch_loss, targets, predictions

In [18]:
# Push model to gpu
model = model.to(device)
# Define the optimizer and the learning rate
optimizer = AdamW(model.parameters(), lr = 2e-5)

best_val_loss = float('inf')
best_epoch = -1
train_losses=[]
val_losses=[]
epochs = 5
# Define the number of epochs to wait for early stopping
patience = 3

# Train the model
for epoch in range(epochs):     
  print('\n Epoch {:} / {:}'.format(epoch + 1, epochs))    
  train_loss = training()
  val_loss, val_targets, val_predictions = evaluate()

  train_losses.append(train_loss)
  val_losses.append(val_loss)

  print("\nTraining Loss:", train_loss)
  print("Validation Loss:", val_loss)
  # Calculate the validation F1 score for the current epoch
  f1 = f1_score(val_targets, val_predictions, average="binary")
  print("F1 score:", round(f1, 3))

  # Save the model with the best validation loss
  if val_loss < best_val_loss:
    best_val_loss = val_loss
    best_epoch = epoch
    torch.save(model.state_dict(), 'saved_weights.pt')

  # Early stopping
  if ((epoch - best_epoch) >= patience):
    print("No improvement in", patience, "epochs. Stopped training.")
    break



 Epoch 1 / 5




Evaluating...

Training Loss: tensor(0.6666, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.6648, device='cuda:0')
F1 score: 0.452

 Epoch 2 / 5




Evaluating...

Training Loss: tensor(0.5860, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.6363, device='cuda:0')
F1 score: 0.602

 Epoch 3 / 5




Evaluating...

Training Loss: tensor(0.4085, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.7090, device='cuda:0')
F1 score: 0.625

 Epoch 4 / 5




Evaluating...

Training Loss: tensor(0.2112, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(0.8468, device='cuda:0')
F1 score: 0.62

 Epoch 5 / 5




Evaluating...

Training Loss: tensor(0.1278, device='cuda:0', grad_fn=<DivBackward0>)
Validation Loss: tensor(1.1329, device='cuda:0')
F1 score: 0.557
No improvement in 3 epochs. Stopped training.


In [19]:
# Save checkpoint to your drive
# Zip
#!zip saved_weights.zip  saved_weights.pt
# Mount
#from google.colab import drive
#drive.mount('/content/gdrive')
# Copy to your drive folder
#!cp -r saved_weights.zip /content/gdrive/MyDrive/

## Inference

#### Load the saved checkpoint

In [20]:
# Use this code to download the model saved in your drive 
# Add the id from the shareable link of the file 
# !gdown --id add_shareable_link_id
# !unzip saved_weights.zip

In [21]:
# Create the model
model_e = BertForSequenceClassification.from_pretrained("bert-base-uncased", output_attentions=True)
# Load pre-trained weights
#checkpoint = torch.load("saved_weights.pt", map_location="cpu")
# Add them to the model
#model_e.load_state_dict(checkpoint)
model_e = model_e.to(device)

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

#### Get predictions for test

In [22]:
# Predict for the test set and save the results
model_e.eval()
test_predictions = []
test_targets = []
test_attentions = []
test_inputs = []

for batch in test_dataloader:
  batch = [t.to(device) for t in batch]
  sent_id, mask, labels = batch
  # Get gold labels
  test_targets.extend(labels.detach().cpu().numpy())
  # Get input words
  test_inputs.append(bert_tokenizer.convert_ids_to_tokens(sent_id.detach().cpu().numpy()[0]))
  with torch.no_grad():
    # Get predictions
    outputs = model_e(sent_id, attention_mask=mask)
    # Apply softmax to the outputs
    output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
    # Get the with the highest probability as the predicted label
    test_predictions.extend(np.argmax(output_probs, axis=1))
    # Get attention weights
    # Attention weights from all layers are returned in a tuple
    # The weights from each layer are in a tensor with shape (batch_size, attention_heads, max_len, max_len)
    test_attentions.append(outputs.attentions)

#### Evaluate

In [23]:
print("F1:", f1_score(test_targets, test_predictions, average="binary"))
print("ACC:", accuracy_score(test_targets, test_predictions))
print("AUPR:", average_precision_score(test_targets, test_predictions))
print("PRECISION:", precision_score(test_targets, test_predictions))
print("RECALL:", recall_score(test_targets, test_predictions))
print("AUC:", roc_auc_score(test_targets, test_predictions))

F1: 0.5544147843942505
ACC: 0.4197860962566845
AUPR: 0.39800977684892314
PRECISION: 0.39823008849557523
RECALL: 0.9121621621621622
AUC: 0.5047536474527625


In [ ]:
#max pooling to generate a fixed sized sentence embedding


#Max Pooling - Take the max value over time for every dimension
def max_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    max_over_time = torch.max(token_embeddings, 1)[0]
    return max_over_time

def avg_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    avg_over_time = torch.mean(token_embeddings, 1)[0]
    return avg_over_time


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other.']

#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)

#Perform pooling. In this case, max pooling
sentence_embeddings = max_pooling(model_output, encoded_input['attention_mask'])
#avg_sentence_embeddings = avg_pooling(model_output, encoded_input['attention_mask'])


print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([-3.5217e-01, -2.3322e-01, -1.9730e-01, -2.6875e-01, -1.0000e+09,
        -1.5048e-01], device='cuda:0')


In [ ]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([-3.5217e-01, -2.3322e-01, -1.9730e-01, -2.6875e-01, -1.0000e+09,
        -1.5048e-01]): 5


In [ ]:
#CLS token of each input represents the sentence embedding


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other']


#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model(**encoded_input)
    #model_output = model_output.to(device)
    
sentence_embeddings = model_output[0][:,0] #Take the first token ([CLS]) from each sentence 

print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([0.3710, 0.9909, 2.4635, 1.4161, 0.8924, 0.4561], device='cuda:0')


In [ ]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([0.3710, 0.9909, 2.4635, 1.4161, 0.8924, 0.4561]): 2


## Attention analysis

In [ ]:
# Get attention heatmaps
import matplotlib
from IPython.core.display import display, HTML
def colorize(words, color_array):
    cmap=matplotlib.cm.Reds
    template = '<span class="barcode"; style="color: black; background-color: {}">{}</span>'
    colored_string = ''
    for word, color in zip(words, color_array):
        color = matplotlib.colors.rgb2hex(cmap(color)[:3])
        colored_string += template.format(color, '&nbsp' + word + '&nbsp')
    return colored_string

#### What does the CLS token attend to?




In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [0,1,2]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    for h, head in enumerate(attention):
      print("Head", h+1)
      # Get the attention for the cls token
      encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
      encoded_tokens = encoded_tokens.to(device)
      with torch.no_grad():
        model_output1 = model_e(**encoded_tokens)
        tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
        tokens_embeddings = tokens_embeddings.cpu()
        cls_attentions = head[0]
        display(HTML(colorize(tokens, cls_attentions)))
        print("Tokens embeddings:")
        print(tokens_embeddings)
        arg = argmax(tokens_embeddings)
        print('arg max of %s: %d' % (tokens_embeddings, arg))

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -0.2076, -0.4744, -0.1333, -0.1959, -0.4651,
        -0.4356, -0.4422, -0.2983, -0.2218, -0.4224, -0.3163, -0.2839, -0.3842,
        -0.2896, -0.4486, -0.1518, -0.3528, -0.4505, -0.3925, -0.3167, -0.4224,
        -0.3598, -0.3842, -0.4367, -0.0990, -0.3438, -0.6103, -0.4486, -0.1518,
        -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -

Tokens embeddings:
tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -0.2076, -0.4744, -0.1333, -0.1959, -0.4651,
        -0.4356, -0.4422, -0.2983, -0.2218, -0.4224, -0.3163, -0.2839, -0.3842,
        -0.2896, -0.4486, -0.1518, -0.3528, -0.4505, -0.3925, -0.3167, -0.4224,
        -0.3598, -0.3842, -0.4367, -0.0990, -0.3438, -0.6103, -0.4486, -0.1518,
        -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -

Tokens embeddings:
tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -0.2076, -0.4744, -0.1333, -0.1959, -0.4651,
        -0.4356, -0.4422, -0.2983, -0.2218, -0.4224, -0.3163, -0.2839, -0.3842,
        -0.2896, -0.4486, -0.1518, -0.3528, -0.4505, -0.3925, -0.3167, -0.4224,
        -0.3598, -0.3842, -0.4367, -0.0990, -0.3438, -0.6103, -0.4486, -0.1518,
        -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -

Tokens embeddings:
tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -0.2076, -0.4744, -0.1333, -0.1959, -0.4651,
        -0.4356, -0.4422, -0.2983, -0.2218, -0.4224, -0.3163, -0.2839, -0.3842,
        -0.2896, -0.4486, -0.1518, -0.3528, -0.4505, -0.3925, -0.3167, -0.4224,
        -0.3598, -0.3842, -0.4367, -0.0990, -0.3438, -0.6103, -0.4486, -0.1518,
        -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.4396, -0.3814, -0.4744, -0.3731, -0.3842, -0.4739, -0.4287,
        -0.3741, -0.4744, -0.2325, -

...

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -0.4744, -0.2522, -0.2663, -0.4372, -0.3791,
        -0.0990, -0.1449, -0.1676, -0.2734, -0.2076, -0.3292, -0.4407, -0.4382,
        -0.3741, -0.4744, -0.4043, -0.2076, -0.5139, -0.4190, -0.4720, -0.4894,
        -0.3842, -0.4006, -0.4706, -0.3654, -0.3741, -0.3651, -0.4744, -0.2589,
        -0.4119, -0.4338, -0.4119, -0.4119, -0.3456, -0.3784, -0.4119, -0.4119,
        -0.3753, -0.3944, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -0.4744, -0.2522, -0.2663, -0.4372, -0.3791,
        -0.0990, -0.1449, -0.1676, -0.2734, -0.2076, -0.3292, -0.4407, -0.4382,
        -0.3741, -0.4744, -0.4043, -0.2076, -0.5139, -0.4190, -0.4720, -0.4894,
        -0.3842, -0.4006, -0.4706, -0.3654, -0.3741, -0.3651, -0.4744, -0.2589,
        -0.4119, -0.4338, -0.4119, -0.4119, -0.3456, -0.3784, -0.4119, -0.4119,
        -0.3753, -0.3944, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -0.4744, -0.2522, -0.2663, -0.4372, -0.3791,
        -0.0990, -0.1449, -0.1676, -0.2734, -0.2076, -0.3292, -0.4407, -0.4382,
        -0.3741, -0.4744, -0.4043, -0.2076, -0.5139, -0.4190, -0.4720, -0.4894,
        -0.3842, -0.4006, -0.4706, -0.3654, -0.3741, -0.3651, -0.4744, -0.2589,
        -0.4119, -0.4338, -0.4119, -0.4119, -0.3456, -0.3784, -0.4119, -0.4119,
        -0.3753, -0.3944, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -0.4744, -0.2522, -0.2663, -0.4372, -0.3791,
        -0.0990, -0.1449, -0.1676, -0.2734, -0.2076, -0.3292, -0.4407, -0.4382,
        -0.3741, -0.4744, -0.4043, -0.2076, -0.5139, -0.4190, -0.4720, -0.4894,
        -0.3842, -0.4006, -0.4706, -0.3654, -0.3741, -0.3651, -0.4744, -0.2589,
        -0.4119, -0.4338, -0.4119, -0.4119, -0.3456, -0.3784, -0.4119, -0.4119,
        -0.3753, -0.3944, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -0.4744, -0.2522, -0.2663, -0.4372, -0.3791,
        -0.0990, -0.1449, -0.1676, -0.2734, -0.2076, -0.3292, -0.4407, -0.4382,
        -0.3741, -0.4744, -0.4043, -0.2076, -0.5139, -0.4190, -0.4720, -0.4894,
        -0.3842, -0.4006, -0.4706, -0.3654, -0.3741, -0.3651, -0.4744, -0.2589,
        -0.4119, -0.4338, -0.4119, -0.4119, -0.3456, -0.3784, -0.4119, -0.4119,
        -0.3753, -0.3944, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.4224, -0.3859, -0.3195, -0.4090, -0.2723, -0.4744,
        -0.3042, -0.2753, -0.2076, -

In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [0,1,2,3,4,5,6,7,8,9,10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-1.0233e-02, -4.3960e-01, -1.0000e+09, -3.5217e-01, -3.7311e-01,
        -1.0000e+09, -2.3131e-01, -4.2868e-01, -1.0000e+09, -3.5217e-01,
        -2.3249e-01, -1.0000e+09, -3.5217e-01, -1.3333e-01, -1.0000e+09,
        -3.2490e-01, -4.3563e-01, -1.0000e+09, -2.9826e-01, -2.2176e-01,
        -1.0000e+09, -2.8190e-01, -2.8394e-01, -1.0000e+09, -1.6137e-01,
        -4.4856e-01, -1.0000e+09, -2.7131e-01, -4.5053e-01, -1.0000e+09,
        -1.6481e-01, -4.2241e-01, -1.0000e+09, -2.8151e-01, -4.3667e-01,
        -1.0000e+09, -1.8529e-01, -6.1033e-01, -1.0000e+09, -1.3764e-01,
        -2.8116e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -4.3960e-01, -1.0000e+09, -3.5217e-01, -3.7311e-01,
        -1.0000e+09, -2.3131e-01, -4.2868e-01, -1.0000e+09, -3.5217e-01,
        -2.3249e-01, -1.0000e+09, -3.5217e-01, -1.3333e-01, -1.0000e+09,
        -3.2490e-01, -4.3563e-01, -1.0000e+09, -2.9826e-01, -2.2176e-01,
        -1.0000e+09, -2.8190e-01, -2.8394e-01, -1.0000e+09, -1.6137e-01,
        -4.4856e-01, -1.0000e+09, -2.7131e-01, -4.5053e-01, -1.0000e+09,
        -1.6481e-01, -4.2241e-01, -1.0000e+09, -2.8151e-01, -4.3667e-01,
        -1.0000e+09, -1.8529e-01, -6.1033e-01, -1.0000e+09, -1.3764e-01,
        -2.8116e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -4.3960e-01, -1.0000e+09, -3.5217e-01, -3.7311e-01,
        -1.0000e+09, -2.3131e-01, -4.2868e-01, -1.0000e+09, -3.5217e-01,
        -2.3249e-01, -1.0000e+09, -3.5217e-01, -1.3333e-01, -1.0000e+09,
        -3.2490e-01, -4.3563e-01, -1.0000e+09, -2.9826e-01, -2.2176e-01,
        -1.0000e+09, -2.8190e-01, -2.8394e-01, -1.0000e+09, -1.6137e-01,
        -4.4856e-01, -1.0000e+09, -2.7131e-01, -4.5053e-01, -1.0000e+09,
        -1.6481e-01, -4.2241e-01, -1.0000e+09, -2.8151e-01, -4.3667e-01,
        -1.0000e+09, -1.8529e-01, -6.1033e-01, -1.0000e+09, -1.3764e-01,
        -2.8116e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -4.3960e-01, -1.0000e+09, -3.5217e-01, -3.7311e-01,
        -1.0000e+09, -2.3131e-01, -4.2868e-01, -1.0000e+09, -3.5217e-01,
        -2.3249e-01, -1.0000e+09, -3.5217e-01, -1.3333e-01, -1.0000e+09,
        -3.2490e-01, -4.3563e-01, -1.0000e+09, -2.9826e-01, -2.2176e-01,
        -1.0000e+09, -2.8190e-01, -2.8394e-01, -1.0000e+09, -1.6137e-01,
        -4.4856e-01, -1.0000e+09, -2.7131e-01, -4.5053e-01, -1.0000e+09,
        -1.6481e-01, -4.2241e-01, -1.0000e+09, -2.8151e-01, -4.3667e-01,
        -1.0000e+09, -1.8529e-01, -6.1033e-01, -1.0000e+09, -1.3764e-01,
        -2.8116e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

...

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -3.0050e-01, -3.1954e-01,
        -1.0000e+09, -1.6655e-01, -4.7442e-01, -1.0000e+09, -2.7530e-01,
        -2.0761e-01, -1.0000e+09, -2.0532e-01, -2.6632e-01, -1.0000e+09,
        -3.0787e-01, -9.9006e-02, -1.0000e+09, -1.6760e-01, -2.7339e-01,
        -1.0000e+09, -2.4218e-01, -4.4074e-01, -1.0000e+09, -3.1394e-01,
        -4.7442e-01, -1.0000e+09, -9.0318e-02, -5.1385e-01, -1.0000e+09,
        -3.1753e-01, -4.8938e-01, -1.0000e+09, -3.1688e-01, -4.7065e-01,
        -1.0000e+09, -3.1394e-01, -3.6515e-01, -1.0000e+09, -2.4115e-01,
        -4.1190e-01, -1.0000e+09, -1.5565e-01, -4.1190e-01, -1.0000e+09,
        -1.3439e-01, -4.1190e-01, -1.0000e+09, -2.7412e-01, -3.9437e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -3.0050e-01, -3.1954e-01,
        -1.0000e+09, -1.6655e-01, -4.7442e-01, -1.0000e+09, -2.7530e-01,
        -2.0761e-01, -1.0000e+09, -2.0532e-01, -2.6632e-01, -1.0000e+09,
        -3.0787e-01, -9.9006e-02, -1.0000e+09, -1.6760e-01, -2.7339e-01,
        -1.0000e+09, -2.4218e-01, -4.4074e-01, -1.0000e+09, -3.1394e-01,
        -4.7442e-01, -1.0000e+09, -9.0318e-02, -5.1385e-01, -1.0000e+09,
        -3.1753e-01, -4.8938e-01, -1.0000e+09, -3.1688e-01, -4.7065e-01,
        -1.0000e+09, -3.1394e-01, -3.6515e-01, -1.0000e+09, -2.4115e-01,
        -4.1190e-01, -1.0000e+09, -1.5565e-01, -4.1190e-01, -1.0000e+09,
        -1.3439e-01, -4.1190e-01, -1.0000e+09, -2.7412e-01, -3.9437e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -3.0050e-01, -3.1954e-01,
        -1.0000e+09, -1.6655e-01, -4.7442e-01, -1.0000e+09, -2.7530e-01,
        -2.0761e-01, -1.0000e+09, -2.0532e-01, -2.6632e-01, -1.0000e+09,
        -3.0787e-01, -9.9006e-02, -1.0000e+09, -1.6760e-01, -2.7339e-01,
        -1.0000e+09, -2.4218e-01, -4.4074e-01, -1.0000e+09, -3.1394e-01,
        -4.7442e-01, -1.0000e+09, -9.0318e-02, -5.1385e-01, -1.0000e+09,
        -3.1753e-01, -4.8938e-01, -1.0000e+09, -3.1688e-01, -4.7065e-01,
        -1.0000e+09, -3.1394e-01, -3.6515e-01, -1.0000e+09, -2.4115e-01,
        -4.1190e-01, -1.0000e+09, -1.5565e-01, -4.1190e-01, -1.0000e+09,
        -1.3439e-01, -4.1190e-01, -1.0000e+09, -2.7412e-01, -3.9437e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -3.0050e-01, -3.1954e-01,
        -1.0000e+09, -1.6655e-01, -4.7442e-01, -1.0000e+09, -2.7530e-01,
        -2.0761e-01, -1.0000e+09, -2.0532e-01, -2.6632e-01, -1.0000e+09,
        -3.0787e-01, -9.9006e-02, -1.0000e+09, -1.6760e-01, -2.7339e-01,
        -1.0000e+09, -2.4218e-01, -4.4074e-01, -1.0000e+09, -3.1394e-01,
        -4.7442e-01, -1.0000e+09, -9.0318e-02, -5.1385e-01, -1.0000e+09,
        -3.1753e-01, -4.8938e-01, -1.0000e+09, -3.1688e-01, -4.7065e-01,
        -1.0000e+09, -3.1394e-01, -3.6515e-01, -1.0000e+09, -2.4115e-01,
        -4.1190e-01, -1.0000e+09, -1.5565e-01, -4.1190e-01, -1.0000e+09,
        -1.3439e-01, -4.1190e-01, -1.0000e+09, -2.7412e-01, -3.9437e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -3.0050e-01, -3.1954e-01,
        -1.0000e+09, -1.6655e-01, -4.7442e-01, -1.0000e+09, -2.7530e-01,
        -2.0761e-01, -1.0000e+09, -2.0532e-01, -2.6632e-01, -1.0000e+09,
        -3.0787e-01, -9.9006e-02, -1.0000e+09, -1.6760e-01, -2.7339e-01,
        -1.0000e+09, -2.4218e-01, -4.4074e-01, -1.0000e+09, -3.1394e-01,
        -4.7442e-01, -1.0000e+09, -9.0318e-02, -5.1385e-01, -1.0000e+09,
        -3.1753e-01, -4.8938e-01, -1.0000e+09, -3.1688e-01, -4.7065e-01,
        -1.0000e+09, -3.1394e-01, -3.6515e-01, -1.0000e+09, -2.4115e-01,
        -4.1190e-01, -1.0000e+09, -1.5565e-01, -4.1190e-01, -1.0000e+09,
        -1.3439e-01, -4.1190e-01, -1.0000e+09, -2.7412e-01, -3.9437e-01,
        -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02, -1.0184e-02,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -0.3957, -0.4119, -0.4338, -0.4879, -0.4043,
        -0.4261, -0.4468, -0.4744, -0.1959, -0.4119, -0.4338, -0.3072, -0.1870,
        -0.4462, -0.4009, -0.3814, -0.4744, -0.1356, -0.2218, -0.4744, -0.4416,
        -0.2950, -0.4054, -0.3218, -0.4119, -0.3013, -0.2779, -0.2326, -0.1740,
        -0.3682, -0.3676, -0.3366, -0.3311, -0.4309, -0.4224, -0.5198, -0.4457,
        -0.4385, -0.3412, -0.2329, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -0.3957, -0.4119, -0.4338, -0.4879, -0.4043,
        -0.4261, -0.4468, -0.4744, -0.1959, -0.4119, -0.4338, -0.3072, -0.1870,
        -0.4462, -0.4009, -0.3814, -0.4744, -0.1356, -0.2218, -0.4744, -0.4416,
        -0.2950, -0.4054, -0.3218, -0.4119, -0.3013, -0.2779, -0.2326, -0.1740,
        -0.3682, -0.3676, -0.3366, -0.3311, -0.4309, -0.4224, -0.5198, -0.4457,
        -0.4385, -0.3412, -0.2329, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -0.3957, -0.4119, -0.4338, -0.4879, -0.4043,
        -0.4261, -0.4468, -0.4744, -0.1959, -0.4119, -0.4338, -0.3072, -0.1870,
        -0.4462, -0.4009, -0.3814, -0.4744, -0.1356, -0.2218, -0.4744, -0.4416,
        -0.2950, -0.4054, -0.3218, -0.4119, -0.3013, -0.2779, -0.2326, -0.1740,
        -0.3682, -0.3676, -0.3366, -0.3311, -0.4309, -0.4224, -0.5198, -0.4457,
        -0.4385, -0.3412, -0.2329, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -

Tokens embeddings:
tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -0.3957, -0.4119, -0.4338, -0.4879, -0.4043,
        -0.4261, -0.4468, -0.4744, -0.1959, -0.4119, -0.4338, -0.3072, -0.1870,
        -0.4462, -0.4009, -0.3814, -0.4744, -0.1356, -0.2218, -0.4744, -0.4416,
        -0.2950, -0.4054, -0.3218, -0.4119, -0.3013, -0.2779, -0.2326, -0.1740,
        -0.3682, -0.3676, -0.3366, -0.3311, -0.4309, -0.4224, -0.5198, -0.4457,
        -0.4385, -0.3412, -0.2329, -0.2812, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.3741, -0.3037, -0.2723, -0.4744, -0.3792, -0.3842, -0.4224,
        -0.5023, -0.2076, -0.4744, -

...

Tokens embeddings:
tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -0.4119, -0.4724, -0.4715, -0.4550, -0.4422,
        -0.4477, -0.5039, -0.3573, -0.4513, -0.3308, -0.0990, -0.4119, -0.2812,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -

Tokens embeddings:
tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -0.4119, -0.4724, -0.4715, -0.4550, -0.4422,
        -0.4477, -0.5039, -0.3573, -0.4513, -0.3308, -0.0990, -0.4119, -0.2812,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -

Tokens embeddings:
tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -0.4119, -0.4724, -0.4715, -0.4550, -0.4422,
        -0.4477, -0.5039, -0.3573, -0.4513, -0.3308, -0.0990, -0.4119, -0.2812,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -

Tokens embeddings:
tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -0.4119, -0.4724, -0.4715, -0.4550, -0.4422,
        -0.4477, -0.5039, -0.3573, -0.4513, -0.3308, -0.0990, -0.4119, -0.2812,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -

Tokens embeddings:
tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -0.4119, -0.4724, -0.4715, -0.4550, -0.4422,
        -0.4477, -0.5039, -0.3573, -0.4513, -0.3308, -0.0990, -0.4119, -0.2812,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729, -0.3729,
        -0.3729, -0.3729, -0.3729, -0.3729, -0.3729])
arg max of tensor([-0.3412, -0.2209, -0.2723, -0.2978, -0.4744, -0.3401, -0.4287, -0.4224,
        -0.3701, -0.3226, -0.4119, -

In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -1.6655e-01, -4.7442e-01,
        -1.0000e+09, -2.8151e-01, -4.2241e-01, -1.0000e+09, -9.0318e-02,
        -4.7442e-01, -1.0000e+09, -1.5565e-01, -4.3384e-01, -1.0000e+09,
        -3.6203e-01, -4.2606e-01, -1.0000e+09, -3.5217e-01, -1.9592e-01,
        -1.0000e+09, -2.8116e-01, -3.0724e-01, -1.0000e+09, -2.9739e-01,
        -4.0092e-01, -1.0000e+09, -3.5217e-01, -1.3561e-01, -1.0000e+09,
        -3.5217e-01, -4.4164e-01, -1.0000e+09, -3.2856e-01, -3.2176e-01,
        -1.0000e+09, -1.7591e-01, -2.7788e-01, -1.0000e+09, -5.3662e-02,
        -3.6822e-01, -1.0000e+09, -2.1012e-01, -3.3107e-01, -1.0000e+09,
        -2.8299e-01, -5.1984e-01, -1.0000e+09, -2.9988e-01, -3.4121e-01,
        -1.0000e+09,  1.5462e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -1.6655e-01, -4.7442e-01,
        -1.0000e+09, -2.8151e-01, -4.2241e-01, -1.0000e+09, -9.0318e-02,
        -4.7442e-01, -1.0000e+09, -1.5565e-01, -4.3384e-01, -1.0000e+09,
        -3.6203e-01, -4.2606e-01, -1.0000e+09, -3.5217e-01, -1.9592e-01,
        -1.0000e+09, -2.8116e-01, -3.0724e-01, -1.0000e+09, -2.9739e-01,
        -4.0092e-01, -1.0000e+09, -3.5217e-01, -1.3561e-01, -1.0000e+09,
        -3.5217e-01, -4.4164e-01, -1.0000e+09, -3.2856e-01, -3.2176e-01,
        -1.0000e+09, -1.7591e-01, -2.7788e-01, -1.0000e+09, -5.3662e-02,
        -3.6822e-01, -1.0000e+09, -2.1012e-01, -3.3107e-01, -1.0000e+09,
        -2.8299e-01, -5.1984e-01, -1.0000e+09, -2.9988e-01, -3.4121e-01,
        -1.0000e+09,  1.5462e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -1.6655e-01, -4.7442e-01,
        -1.0000e+09, -2.8151e-01, -4.2241e-01, -1.0000e+09, -9.0318e-02,
        -4.7442e-01, -1.0000e+09, -1.5565e-01, -4.3384e-01, -1.0000e+09,
        -3.6203e-01, -4.2606e-01, -1.0000e+09, -3.5217e-01, -1.9592e-01,
        -1.0000e+09, -2.8116e-01, -3.0724e-01, -1.0000e+09, -2.9739e-01,
        -4.0092e-01, -1.0000e+09, -3.5217e-01, -1.3561e-01, -1.0000e+09,
        -3.5217e-01, -4.4164e-01, -1.0000e+09, -3.2856e-01, -3.2176e-01,
        -1.0000e+09, -1.7591e-01, -2.7788e-01, -1.0000e+09, -5.3662e-02,
        -3.6822e-01, -1.0000e+09, -2.1012e-01, -3.3107e-01, -1.0000e+09,
        -2.8299e-01, -5.1984e-01, -1.0000e+09, -2.9988e-01, -3.4121e-01,
        -1.0000e+09,  1.5462e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

Tokens embeddings:
tensor([-1.0233e-02, -3.7405e-01, -1.0000e+09, -1.6655e-01, -4.7442e-01,
        -1.0000e+09, -2.8151e-01, -4.2241e-01, -1.0000e+09, -9.0318e-02,
        -4.7442e-01, -1.0000e+09, -1.5565e-01, -4.3384e-01, -1.0000e+09,
        -3.6203e-01, -4.2606e-01, -1.0000e+09, -3.5217e-01, -1.9592e-01,
        -1.0000e+09, -2.8116e-01, -3.0724e-01, -1.0000e+09, -2.9739e-01,
        -4.0092e-01, -1.0000e+09, -3.5217e-01, -1.3561e-01, -1.0000e+09,
        -3.5217e-01, -4.4164e-01, -1.0000e+09, -3.2856e-01, -3.2176e-01,
        -1.0000e+09, -1.7591e-01, -2.7788e-01, -1.0000e+09, -5.3662e-02,
        -3.6822e-01, -1.0000e+09, -2.1012e-01, -3.3107e-01, -1.0000e+09,
        -2.8299e-01, -5.1984e-01, -1.0000e+09, -2.9988e-01, -3.4121e-01,
        -1.0000e+09,  1.5462e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02,
        -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01, -1.0000e+09,
        -1.0184e-02, -3.7285e-01, -1.0000e+09, -1.0184e-02, -3.7285e-01,
        -1.0000e+09, -1.0184e-02

...

Tokens embeddings:
tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -0.1557, -0.2735, -0.2193, -0.3281, -0.3628,
        -0.3012, -0.3432, -0.2139, -0.3356, -0.2955,  0.0443, -0.1557,  0.0155,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102])
arg max of tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -

Tokens embeddings:
tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -0.1557, -0.2735, -0.2193, -0.3281, -0.3628,
        -0.3012, -0.3432, -0.2139, -0.3356, -0.2955,  0.0443, -0.1557,  0.0155,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102])
arg max of tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -

Tokens embeddings:
tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -0.1557, -0.2735, -0.2193, -0.3281, -0.3628,
        -0.3012, -0.3432, -0.2139, -0.3356, -0.2955,  0.0443, -0.1557,  0.0155,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102])
arg max of tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -

Tokens embeddings:
tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -0.1557, -0.2735, -0.2193, -0.3281, -0.3628,
        -0.3012, -0.3432, -0.2139, -0.3356, -0.2955,  0.0443, -0.1557,  0.0155,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102])
arg max of tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -

Tokens embeddings:
tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -0.1557, -0.2735, -0.2193, -0.3281, -0.3628,
        -0.3012, -0.3432, -0.2139, -0.3356, -0.2955,  0.0443, -0.1557,  0.0155,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102, -0.0102,
        -0.0102, -0.0102, -0.0102, -0.0102, -0.0102])
arg max of tensor([-0.0102, -0.2124, -0.1665, -0.2569, -0.3522, -0.2519, -0.2705, -0.2830,
        -0.2825, -0.3074, -0.1557, -

In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))